# $MAPF_R$ environment

$MAPF_R$ environment: a graph $G=(V,E)$, each node is associated with a location in $\mathbb{R}^d$ space, $d\in\{1,2,3\}$. Moreover, each node has a self-loop edge, that is $(s,s)\in E$ for all $s\in V$.

# Definition of a motion plan in $MAPF_R$ environment:

A motion plan is a sequence of (node, time) pairs 
$$
    plan = \{(s_i,t_i): i = 0,1,\ldots, K\}
$$

where $s_i\in V, (s_i,s_{i+1})\in E$, and $t_{i+1}\geq t_i$. An agent following such a plan travels from $s_i$ to $s_{i+1}$ at constant velocity during the time interval $[t_i,t_{i+1}]$. If $s_i=s_{i+1}$, then the agent stays at the same node for the corresponding period.

In [1]:
import networkx as nx
from matplotlib import pyplot as plt
import numpy as np

import sys
sys.path.append('../')

sys.path.append('../../')

from panav.util import interpolate_positions

from panav.SIPP import compute_safe_intervals

from matplotlib.animation import FuncAnimation

from IPython.display import HTML, display


from panav.viz import animate_MAPF_R

%load_ext autoreload
%autoreload 2

In [2]:
node_locs = np.array([[0,1],
                      [0,-1],
                      [1,0],
                      [2,0],
                      [3,0],
                      [4,0],
                      [5,1],
                      [5,-1]])
N = len(node_locs)

G = nx.DiGraph()
G.add_nodes_from(range(N))
edges = [(0,2),
          (1,2),
          (2,3),
          (3,4),
          (4,5),
          (5,6),
          (5,7)]

G.add_edges_from(edges)
G.add_edges_from(e[::-1] for e in edges)

# We manually add the bi-directional edges here, because
# using nx.to_directed(a undirected graph) causes issue when accessing edge values.

In [3]:
bloating_r = 0.2

v_max = 1
nx.set_edge_attributes(G,
                       {e:np.linalg.norm(node_locs[e[0]]-node_locs[e[1]])/v_max\
                          for e in G.edges},
                       'weight')

G_path = [0,2,3,4,5,6]
G_path.reverse()
start_node = G_path[0]
goal_node = G_path[-1]

G_plan = [(start_node,0)]

agent_loc = node_locs[start_node]
t = 0
wait_pos = -1
wait_t = 3.5
for i in range(len(G_path)-1):
    t+=G.edges[G_path[i],G_path[i+1]]['weight']
    G_plan.append((G_path[i+1],t))
    if i==wait_pos:
        t+=wait_t
        G_plan.append((G_path[i+1],t))
    

dt = 0.1


In [7]:
anim = animate_MAPF_R(G,node_locs,[G_plan],[],dt,bloating_r)
display(HTML(anim.to_jshtml()))
plt.close() 

In [ ]:
obs_traj = [] 

for i in range(len(G_plan)-1):
    obs_traj.append((G_plan[i][0],G_plan[i+1][0],
                     G_plan[i][1],G_plan[i+1][1]))

v_max = 1.0

# SIPP

In [8]:
from panav.SIPP import SIPP, G_plan_to_obs_traj
start = 1
goal = 7
obs_traj = G_plan_to_obs_traj(G_plan)
path = SIPP(G,node_locs,start,goal, obs_traj, v_max, bloating_r)

# Animation

In [10]:
anim = animate_MAPF_R(G,node_locs,[G_plan],[path],dt,bloating_r)
display(HTML(anim.to_jshtml()))
plt.close() 